# Fly Me : flights booking chatbot

**Fly Me** is a travel agency offering all-inclusive booking services for private or professional customers.

In this project, we want to create a **ChatBot** that will help users to book their trip.
This task requires to solve multiple challenges such as _Language Understanding_ (identify the intent of a user), _Entities extraction_ (identify relevant information), User Experience (interact in a relevant and appropriate manner).

We will use the [Azure Frames Dataset](https://www.microsoft.com/en-us/research/project/frames-dataset/ "Azure Frames Dataset") to train a bot to understand the **intention** of a user during a dialog, and identify the relevant **entities**.

In our case, the _intention_ will be the **Booking** of a trip, and the entities that we will be looking for are :

- city of origin (`or_city`)
- city of destination (`dst_city`)
- start date of the trip (`str_date`)
- end date of the trip (`end_date`)
- budget of the trip (`budget`)

In this notebook, we will simply perform an **Exploratory Data Analysis** of our dataset.


This is the project architecture in production : 

![center-img h:450px](../docs/img/architecture.drawio.png "Current MVP architecture")


In [1]:
## Download and extract dataset files

!cd .. && make dataset && cd notebooks

>>> Downloading and saving data files...
Data files already downloaded.
>>> OK.



In [3]:
## Import and configure libraries

import json
import warnings
from pathlib import Path

import modin.pandas as pd
import pandas
import plotly.io as pio
from pandas_profiling import ProfileReport
from tqdm import tqdm

warnings.filterwarnings("ignore", category=UserWarning)
warnings.filterwarnings("ignore", category=FutureWarning)


pio.renderers.default = "notebook"


pd.options.plotting.backend = "plotly"

# Set constants
DATA_PATH = Path("../data")
FRAMES_JSON_PATH = Path(DATA_PATH, "raw/frames.json")


In [4]:
## Load the dataset in a Pandas Dataframe (in memory)

raw_data = pd.read_json(FRAMES_JSON_PATH)

raw_data.describe(include="all")


[codecarbon INFO @ 18:20:35] Energy consumed for RAM : 0.000024 kWh. RAM Power : 5.7580060958862305 W
[codecarbon INFO @ 18:20:35] Energy consumed for all CPUs : 0.000000 kWh. All CPUs Power : 0.0 W
[codecarbon INFO @ 18:20:35] 0.000024 kWh of electricity used since the begining.


user_id                                              turns  \
count        1369                                               1369   
unique         11                                               1369   
top     U22K1SX9N  [{'text': 'I'd like to book a trip to Atlantis...   
freq          345                                                  1   

        wizard_id                                    id  \
count        1369                                  1369   
unique         12                                  1369   
top     U21T9NMKM  e2c0fc6c-2134-4891-8353-ef16d8412c9a   
freq          301                                     1   

                                                   labels  
count                                                1369  
unique                                                 16  
top     {'userSurveyRating': 5.0, 'wizardSurveyTaskSuc...  
freq                                                  929

The dataset is composed of **1369** annotated **dialogs** (composed of several _turns_) between a bot and a human user trying to **book a flight**.


In [5]:
frames = raw_data[["id", "wizard_id", "user_id"]]
frames[["userSurveyRating", "wizardSurveyTaskSuccessful"]] = [
    [x["userSurveyRating"], x["wizardSurveyTaskSuccessful"]]
    for x in raw_data.labels
]
frames = frames.astype(
    {"userSurveyRating": "float", "wizardSurveyTaskSuccessful": "bool"}
)
frames.describe(include="all")


id  wizard_id    user_id  \
count                                   1369       1369       1369   
unique                                  1369         12         11   
top     e2c0fc6c-2134-4891-8353-ef16d8412c9a  U21T9NMKM  U22K1SX9N   
freq                                       1        301        345   
mean                                     NaN        NaN        NaN   
std                                      NaN        NaN        NaN   
min                                      NaN        NaN        NaN   
25%                                      NaN        NaN        NaN   
50%                                      NaN        NaN        NaN   
75%                                      NaN        NaN        NaN   
max                                      NaN        NaN        NaN   

        userSurveyRating wizardSurveyTaskSuccessful  
count        1366.000000                       1369  
unique               NaN                          2  
top                  NaN                       True  
freq                 NaN                       1287  
mean            4.573419                        NaN  
std             0.839596                        NaN  
min             1.000000                        NaN  
25%             4.000000                        NaN  
50%             5.000000                        NaN  
75%             5.000000                        NaN  
max             5.000000                        NaN

In [6]:
for turn in raw_data["turns"]:
    print()
    print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
    print()

    known_facts = {}
    for i, frame in enumerate(turn):
        print(f'{i} - { frame["author"] } says : \n"{ frame["text"] }"')

        known_facts.update(
            {
                info_key: info[-1]["val"] if not info[-1]["negated"] else None
                for f in frame["labels"]["frames"]
                for info_key, info in f["info"].items()
            }
        )

        print(f"Known facts : \n{known_facts}")
        print()



XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX

0 - user says : 
"I'd like to book a trip to Atlantis from Caprica on Saturday, August 13, 2016 for 8 adults. I have a tight budget of 1700."
Known facts : 
{'intent': 'book', 'budget': '1700.0', 'dst_city': 'Atlantis', 'or_city': 'Caprica', 'str_date': 'august 13', 'n_adults': '8'}

1 - wizard says : 
"Hi...I checked a few options for you, and unfortunately, we do not currently have any trips that meet this criteria.  Would you like to book an alternate travel option?"
Known facts : 
{'intent': 'book', 'budget': '1700.0', 'dst_city': 'Atlantis', 'or_city': 'Caprica', 'str_date': 'august 13', 'n_adults': '8', 'NO_RESULT': True}

2 - user says : 
"Yes, how about going to Neverland from Caprica on August 13, 2016 for 5 adults. For this trip, my budget would be 1900."
Known facts : 
{'intent': 'book', 'budget': '1900.0', 'dst_city': 'Neverland', 'or_city': 'Caprica', 'str_date': 'august 13', 'n_adults': '5', 'NO_RESULT'

We can see the identified **intent** and extracted **entities** for each turn.


In [7]:
if Path(DATA_PATH, "processed/turns.csv").exists():
    turns = pd.read_csv(Path(DATA_PATH, "processed/turns.csv"))

else:
    turns = pd.DataFrame()

    for turn in tqdm(raw_data["turns"]):
        known_facts = {}

        for i, frame in enumerate(turn):
            if frame["author"] == "wizard":
                continue

            turn_dict = {
                "text": frame["text"],
            }

            turn_dict.update(
                {f"old_{key}": value for key, value in known_facts.items()}
            )

            known_facts.update(
                {
                    info_key: info[-1]["val"]
                    if not info[-1]["negated"]
                    else None
                    for f in frame["labels"]["frames"]
                    for info_key, info in f["info"].items()
                }
            )

            turn_dict.update(
                {f"new_{key}": value for key, value in known_facts.items()}
            )

            turns = turns.append(turn_dict, ignore_index=True)

    turns.to_csv(Path(DATA_PATH, "processed/turns.csv"), index=False)

turns


[codecarbon INFO @ 18:20:50] Energy consumed for RAM : 0.000048 kWh. RAM Power : 5.7580060958862305 W
[codecarbon INFO @ 18:20:50] Energy consumed for all CPUs : 0.000000 kWh. All CPUs Power : 0.0 W
[codecarbon INFO @ 18:20:50] 0.000048 kWh of electricity used since the begining.


text new_intent  \
0      I'd like to book a trip to Atlantis from Capri...       book   
1      Yes, how about going to Neverland from Caprica...       book   
2      I have no flexibility for dates... but I can l...       book   
3      I suppose I'll speak with my husband to see if...       book   
4      Hello, I am looking to book a vacation from Go...       book   
...                                                  ...        ...   
10402  5 adults and 7 kids! Yup, the lot of us. We wa...       book   
10403               Oh yes! Between September 12 and 26!       book   
10404  That sounds amazing, and it's within those dat...       book   
10405                               Ok perfect, book me!       book   
10406                                            Thanks!       book   

      new_budget new_dst_city  new_or_city  new_str_date new_n_adults  \
0         1700.0     Atlantis      Caprica     august 13            8   
1         1900.0    Neverland      Caprica     august 13            5   
2         1700.0     Atlantis     Atlantis     august 13            8   
3         1700.0     Atlantis     Atlantis     august 13            8   
4         2100.0   Mos Eisley  Gotham City           NaN          NaN   
...          ...          ...          ...           ...          ...   
10402    32800.0           -1        Tampa           NaN            5   
10403    32800.0           -1        Tampa  september 12            5   
10404    32800.0   Queenstown        Tampa  september 12            5   
10405    32800.0   Queenstown        Tampa  september 12            5   
10406    32800.0   Queenstown        Tampa  september 12            5   

      old_intent old_budget old_dst_city  ... new_count_seat  old_count_seat  \
0            NaN        NaN          NaN  ...            NaN             NaN   
1           book     1700.0     Atlantis  ...            NaN             NaN   
2           book     1900.0    Neverland  ...            NaN             NaN   
3           book     1700.0     Atlantis  ...            NaN             NaN   
4            NaN        NaN          NaN  ...            NaN             NaN   
...          ...        ...          ...  ...            ...             ...   
10402       book        NaN           -1  ...            NaN             NaN   
10403       book    32800.0           -1  ...            NaN             NaN   
10404       book    32800.0           -1  ...            NaN             NaN   
10405       book    32800.0   Queenstown  ...            NaN             NaN   
10406       book    32800.0   Queenstown  ...            NaN             NaN   

       new_dst_city_ok  old_dst_city_ok  new_impl_anaphora  old_impl_anaphora  \
0                  NaN              NaN                NaN                NaN   
1                  NaN              NaN                NaN                NaN   
2                  NaN              NaN                NaN                NaN   
3                  NaN              NaN                NaN                NaN   
4                  NaN              NaN                NaN                NaN   
...                ...              ...                ...                ...   
10402              NaN              NaN                NaN                NaN   
10403              NaN              NaN                NaN                NaN   
10404              NaN              NaN                NaN                NaN   
10405              NaN              NaN                NaN                NaN   
10406              NaN              NaN                NaN                NaN   

       new_str_date_ok  new_end_date_ok old_str_date_ok old_end_date_ok  
0                  NaN              NaN             NaN             NaN  
1                  NaN              NaN             NaN             NaN  
2                  NaN              NaN             NaN             NaN  
3                  NaN              NaN             NaN             NaN  
4                 

In [8]:
turns.describe(include="all")


text new_intent new_budget new_dst_city new_or_city new_str_date  \
count     10407       9362       6229         9631        9620         7430   
unique     9695          1        228          392         339          155   
top     Thanks!       book         -1   Punta Cana          -1           -1   
freq         73       9362       1704          283         174          655   

       new_n_adults old_intent old_budget old_dst_city  ... new_count_seat  \
count          5570       8078       5255         8307  ...              7   
unique           57          1        225          382  ...              1   
top               1       book         -1           -1  ...            two   
freq           2462       8078       1469          257  ...              7   

       old_count_seat new_dst_city_ok old_dst_city_ok new_impl_anaphora  \
count               6               8               7                 5   
unique              1               1               1                 1   
top               two            True            True          category   
freq                6               8               7                 5   

       old_impl_anaphora new_str_date_ok new_end_date_ok old_str_date_ok  \
count                  4               3               3               2   
unique                 1               1               1               1   
top             category            True            True            True   
freq                   4               3               3               2   

       old_end_date_ok  
count                2  
unique               1  
top               True  
freq                 2  

[4 rows x 120 columns]

In [9]:
columns = ["text"] + [
    f"{prefix}_{key}"
    for key in ["or_city", "dst_city", "str_date", "end_date", "budget"]
    for prefix in ["old", "new"]
]
data = turns[columns]

data


text old_or_city  \
0      I'd like to book a trip to Atlantis from Capri...         NaN   
1      Yes, how about going to Neverland from Caprica...     Caprica   
2      I have no flexibility for dates... but I can l...     Caprica   
3      I suppose I'll speak with my husband to see if...    Atlantis   
4      Hello, I am looking to book a vacation from Go...         NaN   
...                                                  ...         ...   
10402  5 adults and 7 kids! Yup, the lot of us. We wa...       Tampa   
10403               Oh yes! Between September 12 and 26!       Tampa   
10404  That sounds amazing, and it's within those dat...       Tampa   
10405                               Ok perfect, book me!       Tampa   
10406                                            Thanks!       Tampa   

       new_or_city old_dst_city new_dst_city  old_str_date  new_str_date  \
0          Caprica          NaN     Atlantis           NaN     august 13   
1          Caprica     Atlantis    Neverland     august 13     august 13   
2         Atlantis    Neverland     Atlantis     august 13     august 13   
3         Atlantis     Atlantis     Atlantis     august 13     august 13   
4      Gotham City          NaN   Mos Eisley           NaN           NaN   
...            ...          ...          ...           ...           ...   
10402        Tampa           -1           -1           NaN           NaN   
10403        Tampa           -1           -1           NaN  september 12   
10404        Tampa           -1   Queenstown  september 12  september 12   
10405        Tampa   Queenstown   Queenstown  september 12  september 12   
10406        Tampa   Queenstown   Queenstown  september 12  september 12   

      old_end_date new_end_date old_budget new_budget  
0              NaN          NaN        NaN     1700.0  
1              NaN          NaN     1700.0     1900.0  
2              NaN          NaN     1900.0     1700.0  
3              NaN          NaN     1700.0     1700.0  
4              NaN          NaN        NaN     2100.0  
...            ...          ...        ...        ...  
10402          NaN          NaN        NaN    32800.0  
10403          NaN           26    32800.0    32800.0  
10404           26           26    32800.0    32800.0  
10405           26           25    32800.0    32800.0  
10406           25           25    32800.0    32800.0  

[10407 rows x 11 columns]

In [10]:
data.describe(include="all")


text old_or_city new_or_city old_dst_city new_dst_city  \
count     10407        8287        9620         8307         9631   
unique     9695         332         339          382          392   
top     Thanks!          -1          -1           -1   Punta Cana   
freq         73         158         174          257          283   

       old_str_date new_str_date old_end_date new_end_date old_budget  \
count          6287         7430         4787         5734       5255   
unique          151          155          129          131        225   
top              -1           -1           -1           -1         -1   
freq            567          655          344          404       1469   

       new_budget  
count        6229  
unique        228  
top            -1  
freq         1704

For each user turn, we can see what the bot has inferred given what it previously knew and what the user said.


In [12]:
## Publish Articles Metadata ProfileReport

profile = ProfileReport(
    pandas.DataFrame(data),
    title="Pandas Profiling Report",
    explorative=True,
    minimal=True,
)
profile.to_file(Path("../docs/profile_report.html"))


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

The dataset profile report is available online : [dataset profile report](https://fleuryc.github.io/OC_AI-Engineer_P10_Flights-booking-chatbot/profile_report.html "dataset profile report")
